In [101]:
import pandas as pd
import numpy as np
import seaborn as sb
import io
import requests
import datetime
import ondemand
from scipy.stats import pearsonr
from pandas.io.common import EmptyDataError
from requests.exceptions import HTTPError
import time
import os
import json
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

In [103]:
all_symbols = list(pd.read_csv('Highest_change_total.csv')['Symbol'])

In [6]:
from multiprocessing import Pool as ThreadPool
from multiprocessing import Manager
class Generate_Leaders():
    def __init__(self): 
        self.pageview_change = dict()
        self.my_date = None
    def get_mkt_cap(self, symbol, start_date, end_date):
        file = pd.read_csv('Highest_change_total.csv')
        try:
            mktcap = float(file.loc[file['Symbol'] == symbol]['Market_Cap(billion)'])
        except:
            return
        return mktcap
    def parallel(self, item):
        try:
            pageview_price = pd.read_csv('pageview_price/pageview_price_{}.csv'.format(item.lower()))
        except FileNotFoundError:
            print('{} has no pageview data!!!'.format(item))
            return
        if pageview_price.empty:
            return
        #print(datetime.datetime.now())
        temp_res = pageview_price.set_index(['Date'])
        try:
            temp_res = temp_res.loc[[self.my_date]]
            temp_res.reset_index(col_fill = 'Date', inplace = True)
        except:
            print('{} has no trading on {}!!!'.format(item, self.my_date))
            return
        if temp_res.loc[0, 'PageView'] < 10:
            print('{} pageview on {} less than 10, skip it.'.format(item, self.my_date))
            return
        temp_res.loc[0, 'Market_Cap(billion)'] = self.get_mkt_cap(item, self.my_date, self.my_date)
        if temp_res['Market_Cap(billion)'].isnull().values.any():
            pass
        else:
            temp_res['Market_Cap(billion)'] = temp_res['Market_Cap(billion)'].round(2)
        self.pageview_change[item] = temp_res 
    def highest_change(self, my_date, symbols):
        self.my_date = my_date
        for i, item in enumerate(symbols):
            if i % 300 == 0:
                print('run well')
                print(i)
            self.parallel(item)

In [105]:
#get business days
from pandas.tseries.offsets import *
daterange1 = pd.date_range('2017-12-01', '2019-01-20', freq=BDay())
daterange1 = list(daterange1.strftime('%Y-%m-%d'))
holidays = ['2017-12-25', '2018-01-01', '2018-01-15', '2018-02-19', '2018-03-30', '2018-05-28', '2018-07-04', '2018-09-03',\
            '2018-11-22', '2018-12-05', '2018-12-25', '2019-01-01']
for each in holidays:
    if each in daterange1:
        daterange1.remove(each)

In [106]:
daterange2 = daterange1[20:271]

In [33]:
#Generate highest change for each day
def highest_change(daterange, all_symbols, cap):
    for i, date in enumerate(daterange):
        print(i)
        print(date)
        leader = Generate_Leaders()
        highest_change = leader.highest_change(date, all_symbols)
        to_combine = pd.DataFrame([])
        for item in all_symbols:
            try:
                temp = leader.pageview_change[item]
            except:
                continue
            to_combine = pd.concat([to_combine, temp], sort = False, ignore_index = True)
        if not os.path.exists(os.path.dirname('leaderlist {}/'.format(date))):
            os.makedirs(os.path.dirname('leaderlist {}/'.format(date)))
        if to_combine.empty:
            print('{} is not trading day!!!'.format(date))
            continue
        highest_change_window1 = to_combine.drop(['PageView_Change_in_Std_3'], axis = 1)
        highest_change_window1['Time_Window'] = 1
        highest_change_window1.sort_values(by = ['PageView_Change_in_Std_1'], ascending = False, inplace = True)
        highest_change_window3 = to_combine.drop(['PageView_Change_in_Std_1'], axis = 1)
        highest_change_window3['Time_Window'] = 3
        highest_change_window3.sort_values(by = ['PageView_Change_in_Std_3'], ascending = False, inplace = True)
        if not os.path.exists(os.path.dirname('leaderlist {}/{}_cap/window_{}_day/'.format(date, cap, 1))):
            os.makedirs(os.path.dirname('leaderlist {}/{}_cap/window_{}_day/'.format(date, cap, 1)))
        if not os.path.exists(os.path.dirname('leaderlist {}/{}_cap/window_{}_day/'.format(date, cap, 3))):
            os.makedirs(os.path.dirname('leaderlist {}/{}_cap/window_{}_day/'.format(date, cap, 3)))    
        highest_change_window1.to_csv('leaderlist {}/{}_cap/window_1_day/{}_cap_highest_change_time_window_1.csv'.\
                                      format(date, cap, cap), index = False)
        highest_change_window3.to_csv('leaderlist {}/{}_cap/window_3_day/{}_cap_highest_change_time_window_3.csv'.\
                                      format(date, cap, cap), index = False)


In [26]:
#copy prior results
main = '/Users/yuying/PAGE_VIEW/Barchart_Final/PAGE_VIEW phase6_top10_trading/'
for date in daterange2:
    for cap in ['small', 'mid', 'large']:
        for win in [1, 3]: 
            temp = pd.read_csv(main + 'leaderlist {}/{}_cap/window_{}_day/{}_cap_highest_change_time_window_{}.csv'.\
                        format(date, cap, win, cap, win))
            if not os.path.exists(os.path.dirname('leaderlist {}/{}_cap/window_{}_day/'.format(date, cap, win))):
                os.makedirs(os.path.dirname('leaderlist {}/{}_cap/window_{}_day/'.format(date, cap, win)))
            temp.to_csv('leaderlist {}/{}_cap/window_{}_day/{}_cap_highest_change_time_window_{}.csv'.\
                                      format(date, cap, win, cap, win), index = False)

In [34]:
highest_change(daterange2, smallcap, 'small')
highest_change(daterange2, midcap, 'mid')
highest_change(daterange2, largecap, 'large')

0
2018-01-02
run well
0
STFC pageview on 2018-01-02 less than 10, skip it.
ACRS pageview on 2018-01-02 less than 10, skip it.
HBB pageview on 2018-01-02 less than 10, skip it.
LMNR pageview on 2018-01-02 less than 10, skip it.
DESP pageview on 2018-01-02 less than 10, skip it.
VGR pageview on 2018-01-02 less than 10, skip it.
TPRE pageview on 2018-01-02 less than 10, skip it.
ATNI pageview on 2018-01-02 less than 10, skip it.
BRSS pageview on 2018-01-02 less than 10, skip it.
GPRK pageview on 2018-01-02 less than 10, skip it.
LIFE pageview on 2018-01-02 less than 10, skip it.
SRLP pageview on 2018-01-02 less than 10, skip it.
MN pageview on 2018-01-02 less than 10, skip it.
IRET pageview on 2018-01-02 less than 10, skip it.
LION pageview on 2018-01-02 less than 10, skip it.
SRCE pageview on 2018-01-02 less than 10, skip it.
KNSL pageview on 2018-01-02 less than 10, skip it.
CPSS pageview on 2018-01-02 less than 10, skip it.
GNK pageview on 2018-01-02 less than 10, skip it.
TRST pagevie

WNC pageview on 2018-01-02 less than 10, skip it.
RTIX pageview on 2018-01-02 less than 10, skip it.
ORN pageview on 2018-01-02 less than 10, skip it.
NERV pageview on 2018-01-02 less than 10, skip it.
OSBC pageview on 2018-01-02 less than 10, skip it.
RVLT pageview on 2018-01-02 less than 10, skip it.
VCYT pageview on 2018-01-02 less than 10, skip it.
ARC pageview on 2018-01-02 less than 10, skip it.
TG pageview on 2018-01-02 less than 10, skip it.
HIFR pageview on 2018-01-02 less than 10, skip it.
CASS pageview on 2018-01-02 less than 10, skip it.
ELF pageview on 2018-01-02 less than 10, skip it.
WMK pageview on 2018-01-02 less than 10, skip it.
JBSS pageview on 2018-01-02 less than 10, skip it.
DEST pageview on 2018-01-02 less than 10, skip it.
REV pageview on 2018-01-02 less than 10, skip it.
PICO pageview on 2018-01-02 less than 10, skip it.
OFIX pageview on 2018-01-02 less than 10, skip it.
HDSN pageview on 2018-01-02 less than 10, skip it.
MAXR pageview on 2018-01-02 less than 1

VSTO pageview on 2018-01-02 less than 10, skip it.
CRAI pageview on 2018-01-02 less than 10, skip it.
OSIR pageview on 2018-01-02 less than 10, skip it.
OSG pageview on 2018-01-02 less than 10, skip it.
KURA pageview on 2018-01-02 less than 10, skip it.
CLXT pageview on 2018-01-02 less than 10, skip it.
HCCI pageview on 2018-01-02 less than 10, skip it.
NWPX pageview on 2018-01-02 less than 10, skip it.
BFS pageview on 2018-01-02 less than 10, skip it.
WAGE pageview on 2018-01-02 less than 10, skip it.
PDS pageview on 2018-01-02 less than 10, skip it.
SHEN pageview on 2018-01-02 less than 10, skip it.
EGLE pageview on 2018-01-02 less than 10, skip it.
CYD pageview on 2018-01-02 less than 10, skip it.
NNBR pageview on 2018-01-02 less than 10, skip it.
CAC pageview on 2018-01-02 less than 10, skip it.
BSET pageview on 2018-01-02 less than 10, skip it.
AMRC pageview on 2018-01-02 less than 10, skip it.
CTT pageview on 2018-01-02 less than 10, skip it.
ALG pageview on 2018-01-02 less than 

BSRR pageview on 2018-01-03 less than 10, skip it.
AKBA pageview on 2018-01-03 less than 10, skip it.
AHH pageview on 2018-01-03 less than 10, skip it.
FLXS pageview on 2018-01-03 less than 10, skip it.
SPOK pageview on 2018-01-03 less than 10, skip it.
QCRH pageview on 2018-01-03 less than 10, skip it.
PDVW pageview on 2018-01-03 less than 10, skip it.
TVTY pageview on 2018-01-03 less than 10, skip it.
LORL pageview on 2018-01-03 less than 10, skip it.
PRFT pageview on 2018-01-03 less than 10, skip it.
FRGI pageview on 2018-01-03 less than 10, skip it.
SAFE pageview on 2018-01-03 less than 10, skip it.
GTY pageview on 2018-01-03 less than 10, skip it.
VNDA pageview on 2018-01-03 less than 10, skip it.
NCBS pageview on 2018-01-03 less than 10, skip it.
NCOM pageview on 2018-01-03 less than 10, skip it.
VRTS pageview on 2018-01-03 less than 10, skip it.
AROC pageview on 2018-01-03 less than 10, skip it.
SENEA pageview on 2018-01-03 less than 10, skip it.
ACBI pageview on 2018-01-03 less

DFRG pageview on 2018-01-03 less than 10, skip it.
FRPH pageview on 2018-01-03 less than 10, skip it.
GSBC pageview on 2018-01-03 less than 10, skip it.
MPVD pageview on 2018-01-03 less than 10, skip it.
MSTR pageview on 2018-01-03 less than 10, skip it.
BELFB pageview on 2018-01-03 less than 10, skip it.
CTWS pageview on 2018-01-03 less than 10, skip it.
DRQ pageview on 2018-01-03 less than 10, skip it.
CSU pageview on 2018-01-03 less than 10, skip it.
QUOT pageview on 2018-01-03 less than 10, skip it.
FLWS pageview on 2018-01-03 less than 10, skip it.
WLDN pageview on 2018-01-03 less than 10, skip it.
TRK pageview on 2018-01-03 less than 10, skip it.
ABTX pageview on 2018-01-03 less than 10, skip it.
NXEO pageview on 2018-01-03 less than 10, skip it.
AT pageview on 2018-01-03 less than 10, skip it.
ARCW pageview on 2018-01-03 less than 10, skip it.
CRAI pageview on 2018-01-03 less than 10, skip it.
OSIR pageview on 2018-01-03 less than 10, skip it.
ADES pageview on 2018-01-03 less th

...

GIB pageview on 2018-11-02 less than 10, skip it.
ETR pageview on 2018-11-02 less than 10, skip it.
ACGL pageview on 2018-11-02 less than 10, skip it.
ROL pageview on 2018-11-02 less than 10, skip it.
213
2018-11-05
run well
0
BGNE pageview on 2018-11-05 less than 10, skip it.
SGEN pageview on 2018-11-05 less than 10, skip it.
BIP pageview on 2018-11-05 less than 10, skip it.
ZBH pageview on 2018-11-05 less than 10, skip it.
AVB pageview on 2018-11-05 less than 10, skip it.
ATH pageview on 2018-11-05 less than 10, skip it.
UDR pageview on 2018-11-05 less than 10, skip it.
CMS pageview on 2018-11-05 less than 10, skip it.
WIT pageview on 2018-11-05 less than 10, skip it.
TU pageview on 2018-11-05 less than 10, skip it.
BXP pageview on 2018-11-05 less than 10, skip it.
EIX pageview on 2018-11-05 less than 10, skip it.
BSAC pageview on 2018-11-05 less than 10, skip it.
ANDX pageview on 2018-11-05 less than 10, skip it.
EXR pageview on 2018-11-05 less than 10, skip it.
VAR pageview on 2018

FNF pageview on 2018-11-14 less than 10, skip it.
ETR pageview on 2018-11-14 less than 10, skip it.
ACGL pageview on 2018-11-14 less than 10, skip it.
PBA pageview on 2018-11-14 less than 10, skip it.
221
2018-11-15
run well
0
WEC pageview on 2018-11-15 less than 10, skip it.
DLR pageview on 2018-11-15 less than 10, skip it.
ZBH pageview on 2018-11-15 less than 10, skip it.
AVB pageview on 2018-11-15 less than 10, skip it.
UDR pageview on 2018-11-15 less than 10, skip it.
CMS pageview on 2018-11-15 less than 10, skip it.
VST pageview on 2018-11-15 less than 10, skip it.
WIT pageview on 2018-11-15 less than 10, skip it.
TU pageview on 2018-11-15 less than 10, skip it.
FITB pageview on 2018-11-15 less than 10, skip it.
BSAC pageview on 2018-11-15 less than 10, skip it.
ANDX pageview on 2018-11-15 less than 10, skip it.
EXR pageview on 2018-11-15 less than 10, skip it.
VAR pageview on 2018-11-15 less than 10, skip it.
ESS pageview on 2018-11-15 less than 10, skip it.
PKG pageview on 2018-

ROL pageview on 2018-11-27 less than 10, skip it.
229
2018-11-28
run well
0
SRE pageview on 2018-11-28 less than 10, skip it.
DTE pageview on 2018-11-28 less than 10, skip it.
LLL pageview on 2018-11-28 less than 10, skip it.
SGEN pageview on 2018-11-28 less than 10, skip it.
DFS pageview on 2018-11-28 less than 10, skip it.
ATH pageview on 2018-11-28 less than 10, skip it.
UDR pageview on 2018-11-28 less than 10, skip it.
CMS pageview on 2018-11-28 less than 10, skip it.
VST pageview on 2018-11-28 less than 10, skip it.
WIT pageview on 2018-11-28 less than 10, skip it.
TU pageview on 2018-11-28 less than 10, skip it.
FITB pageview on 2018-11-28 less than 10, skip it.
BSAC pageview on 2018-11-28 less than 10, skip it.
ANDX pageview on 2018-11-28 less than 10, skip it.
EXR pageview on 2018-11-28 less than 10, skip it.
ESS pageview on 2018-11-28 less than 10, skip it.
GIB pageview on 2018-11-28 less than 10, skip it.
FNF pageview on 2018-11-28 less than 10, skip it.
ETR pageview on 2018-

ACGL pageview on 2018-12-11 less than 10, skip it.
238
2018-12-12
run well
0
SRE pageview on 2018-12-12 less than 10, skip it.
WCG pageview on 2018-12-12 less than 10, skip it.
DTE pageview on 2018-12-12 less than 10, skip it.
BGNE pageview on 2018-12-12 less than 10, skip it.
SGEN pageview on 2018-12-12 less than 10, skip it.
ZBH pageview on 2018-12-12 less than 10, skip it.
ATH pageview on 2018-12-12 less than 10, skip it.
WIT pageview on 2018-12-12 less than 10, skip it.
TU pageview on 2018-12-12 less than 10, skip it.
FITB pageview on 2018-12-12 less than 10, skip it.
BXP pageview on 2018-12-12 less than 10, skip it.
EIX pageview on 2018-12-12 less than 10, skip it.
BSAC pageview on 2018-12-12 less than 10, skip it.
ESS pageview on 2018-12-12 less than 10, skip it.
PKG pageview on 2018-12-12 less than 10, skip it.
GIB pageview on 2018-12-12 less than 10, skip it.
ACGL pageview on 2018-12-12 less than 10, skip it.
239
2018-12-13
run well
0
SRE pageview on 2018-12-13 less than 10, sk

ACGL pageview on 2018-12-21 less than 10, skip it.
PBA pageview on 2018-12-21 less than 10, skip it.
ROL pageview on 2018-12-21 less than 10, skip it.
PSA pageview on 2018-12-21 less than 10, skip it.
246
2018-12-24
run well
0
SRE pageview on 2018-12-24 less than 10, skip it.
WCG pageview on 2018-12-24 less than 10, skip it.
DTE pageview on 2018-12-24 less than 10, skip it.
XEL pageview on 2018-12-24 less than 10, skip it.
MKL pageview on 2018-12-24 less than 10, skip it.
BGNE pageview on 2018-12-24 less than 10, skip it.
SGEN pageview on 2018-12-24 less than 10, skip it.
ZBH pageview on 2018-12-24 less than 10, skip it.
AVB pageview on 2018-12-24 less than 10, skip it.
DISCA pageview on 2018-12-24 less than 10, skip it.
ATH pageview on 2018-12-24 less than 10, skip it.
UDR pageview on 2018-12-24 less than 10, skip it.
VST pageview on 2018-12-24 less than 10, skip it.
RMD pageview on 2018-12-24 less than 10, skip it.
TU pageview on 2018-12-24 less than 10, skip it.
FITB pageview on 201

In [27]:
#Pick the top 10 symbols with highest PageView_Change_in_std and PageView > 10
for win in [1, 3]:
    for date in daterange2:
        print(datetime.datetime.now())
        print(date)
        for cap in ['small', 'mid', 'large']:
            try:
                to_filter = pd.read_csv\
                ('leaderlist {}/{}_cap/window_{}_day/{}_cap_highest_change_time_window_{}.csv'.format(date, cap, win, cap, win))
            except FileNotFoundError:
                continue
            to_filter = to_filter.loc[to_filter['PageView_Change_in_Std_{}'.format(win)] >= 3]
            each = date
            each = each[5:]
            each = each.replace('-', '')
            to_filter = to_filter.head(10)
            to_filter.to_csv\
            ('leaderlist {}/{}_cap/window_{}_day/{}_{}_cap_window_{}_symbols.csv'.format(date, cap, win, each, cap, win), index = False)
            

2019-05-08 13:37:37.746668
2018-01-02
2019-05-08 13:37:37.769357
2018-01-03
2019-05-08 13:37:37.791816
2018-01-04
2019-05-08 13:37:37.807315
2018-01-05
2019-05-08 13:37:37.823862
2018-01-08
2019-05-08 13:37:37.838459
2018-01-09
2019-05-08 13:37:37.853604
2018-01-10
2019-05-08 13:37:37.871268
2018-01-11
2019-05-08 13:37:37.887956
2018-01-12
2019-05-08 13:37:37.903900
2018-01-16
2019-05-08 13:37:37.919845
2018-01-17
2019-05-08 13:37:37.935518
2018-01-18
2019-05-08 13:37:37.953021
2018-01-19
2019-05-08 13:37:37.973786
2018-01-22
2019-05-08 13:37:37.991420
2018-01-23
2019-05-08 13:37:38.007587
2018-01-24
2019-05-08 13:37:38.022601
2018-01-25
2019-05-08 13:37:38.041062
2018-01-26
2019-05-08 13:37:38.057889
2018-01-29
2019-05-08 13:37:38.073781
2018-01-30
2019-05-08 13:37:38.089627
2018-01-31
2019-05-08 13:37:38.105470
2018-02-01
2019-05-08 13:37:38.122354
2018-02-02
2019-05-08 13:37:38.138694
2018-02-05
2019-05-08 13:37:38.154686
2018-02-06
2019-05-08 13:37:38.176114
2018-02-07
2019-05-08 1

2019-05-08 13:37:41.817630
2018-11-21
2019-05-08 13:37:41.835139
2018-11-23
2019-05-08 13:37:41.856444
2018-11-26
2019-05-08 13:37:41.874015
2018-11-27
2019-05-08 13:37:41.895749
2018-11-28
2019-05-08 13:37:41.914638
2018-11-29
2019-05-08 13:37:41.932268
2018-11-30
2019-05-08 13:37:41.948614
2018-12-03
2019-05-08 13:37:41.965820
2018-12-04
2019-05-08 13:37:41.982173
2018-12-06
2019-05-08 13:37:42.000950
2018-12-07
2019-05-08 13:37:42.017499
2018-12-10
2019-05-08 13:37:42.038342
2018-12-11
2019-05-08 13:37:42.058411
2018-12-12
2019-05-08 13:37:42.075924
2018-12-13
2019-05-08 13:37:42.092545
2018-12-14
2019-05-08 13:37:42.109844
2018-12-17
2019-05-08 13:37:42.127552
2018-12-18
2019-05-08 13:37:42.145496
2018-12-19
2019-05-08 13:37:42.162757
2018-12-20
2019-05-08 13:37:42.181931
2018-12-21
2019-05-08 13:37:42.197690
2018-12-24
2019-05-08 13:37:42.213118
2018-12-26
2019-05-08 13:37:42.229727
2018-12-27
2019-05-08 13:37:42.246764
2018-12-28
2019-05-08 13:37:42.266760
2018-12-31
2019-05-08 1

2019-05-08 13:37:45.888525
2018-10-19
2019-05-08 13:37:45.905699
2018-10-22
2019-05-08 13:37:45.921060
2018-10-23
2019-05-08 13:37:45.942143
2018-10-24
2019-05-08 13:37:45.959633
2018-10-25
2019-05-08 13:37:45.977941
2018-10-26
2019-05-08 13:37:45.995590
2018-10-29
2019-05-08 13:37:46.011512
2018-10-30
2019-05-08 13:37:46.026221
2018-10-31
2019-05-08 13:37:46.041511
2018-11-01
2019-05-08 13:37:46.056935
2018-11-02
2019-05-08 13:37:46.072667
2018-11-05
2019-05-08 13:37:46.090750
2018-11-06
2019-05-08 13:37:46.111013
2018-11-07
2019-05-08 13:37:46.127330
2018-11-08
2019-05-08 13:37:46.143960
2018-11-09
2019-05-08 13:37:46.159023
2018-11-12
2019-05-08 13:37:46.176311
2018-11-13
2019-05-08 13:37:46.192614
2018-11-14
2019-05-08 13:37:46.209464
2018-11-15
2019-05-08 13:37:46.225215
2018-11-16
2019-05-08 13:37:46.241808
2018-11-19
2019-05-08 13:37:46.257907
2018-11-20
2019-05-08 13:37:46.275053
2018-11-21
2019-05-08 13:37:46.291041
2018-11-23
2019-05-08 13:37:46.305398
2018-11-26
2019-05-08 1

In [32]:
daterange2.index('2018-01-10')

6

In [33]:
#Generate trading detail for 1-business day
for win in [1, 3]:
    print(win)
    for date in daterange2:
        for cap in ['small', 'mid', 'large']:
            url = 'https://ondemand.websol.barchart.com/getHistory.csv?apikey=onDemand&symbol={}&startDate={}&endDate={}&type=daily&splits=true&nearby=1&jerq=true&exchange=NYSE%2CAMEX%2CNASDAQ'
            trading_day = daterange1[daterange1.index(date) + 1]
            each = date
            each = each[5:]
            each = each.replace('-', '')
            try:
                portfolio = pd.read_csv\
            ('leaderlist {}/{}_cap/window_{}_day/{}_{}_cap_window_{}_symbols.csv'.format(date, cap, win, each, cap, win))
            except FileNotFoundError:
                break
            portfolio = list(portfolio['Symbol'])
            trading_each = trading_day
            trading_each = trading_each[5:]
            trading_each = trading_each.replace('-', '')
            result = pd.DataFrame([], columns = ['symbol', 'win_start', 'win_end', 'actual_pageview', 'average_pageview', \
                                                 'std_100days_rolling', 'actual_pageview_in_std', 'buy_date', 'sell_date', \
                                                 'buy_price', 'sell_price', 'pct_change(%)', 'abs(pct_change(%))', 'window'])
            count = 0
            window_days = []
            while count < win:
                window_days.append(daterange1[daterange1.index(date) - count])
                count += 1
            window_days = window_days[::-1]
            win_start = window_days[0]
            win_end = window_days[-1]
            result['symbol'] = portfolio
            result['win_start'] = str(win_start)[:10]
            result['win_end'] = str(win_end)[:10]
            result['buy_date'] = trading_day
            result['sell_date'] = trading_day
            for i, item in enumerate(portfolio):
                try:
                    price = pd.read_csv(url.format(item, trading_day, trading_day))
                except EmptyDataError:
                    result.loc[result['symbol'] == item, 'buy_price']= 'No Trading'
                    continue
                pageview_price = pd.read_csv('pageview_price/pageview_price_{}.csv'.format(item))
                temp = pageview_price['PageView']
                pageview_price['std_100days_rolling'] = (temp.rolling(100).std()).shift(win)
                pageview_price['mean_100days_rolling'] = (temp.rolling(100).mean()).shift(win)
                total_pageview = 0
                for each in window_days:
                    try:
                        total_pageview += int(pageview_price.loc[pageview_price['Date'] == str(each)[:10]]['PageView'])
                    except:
                        page = pd.read_csv('pageview_daily_2018/pageview_daily_{}.csv'.format(item))
                        total_pageview += int(page.loc[page['date'] == str(each)[:10]]['total_page_views'])
                result.loc[i, 'actual_pageview'] = total_pageview
                result.loc[i, 'average_pageview'] = float(pageview_price.loc[pageview_price['Date'] == str(win_end)[:10]]['mean_100days_rolling'])*win
                result.loc[i, 'std_100days_rolling'] = float(pageview_price.loc[pageview_price['Date'] == str(win_end)[:10]]['std_100days_rolling'])
                result.loc[i, 'actual_pageview_in_std'] = float(pageview_price.loc[pageview_price['Date'] == str(win_end)[:10]]['PageView_Change_in_Std_{}'.format(win)])
                result.loc[i, 'buy_price'] = price.loc[0, 'open']
                result.loc[i, 'sell_price'] = price.loc[0, 'close']
                result.loc[i, 'pct_change(%)'] = (price.loc[0, 'close']/price.loc[0, 'open'] - 1)*100
                result.loc[i, 'abs(pct_change(%))'] = abs((price.loc[0, 'close']/price.loc[0, 'open'] - 1)*100)
                result.loc[i, 'window'] = win
            if not os.path.exists(os.path.dirname('leaderlist {}/{}_cap/window_{}_day/hold_1_day/'.format(date, cap, win))):
                os.makedirs(os.path.dirname('leaderlist {}/{}_cap/window_{}_day/hold_1_day/'.format(date, cap, win)))
            result.to_csv('leaderlist {}/{}_cap/window_{}_day/hold_1_day/{}_{}_cap_window_{}_hold_1_detail.csv'.format(date, cap, win, trading_each, cap, win), index = False)
            
            

3


#to summary the 1-business day strategy results
for win in [1, 3]:
    for cap in ['small', 'mid', 'large']:
        to_combine = pd.DataFrame([])
        for date in daterange2:
            trading_day = daterange1[daterange1.index(date) + 1]
            each = trading_day
            each = each[5:]
            each = each.replace('-', '')
            try:
                temp = pd.read_csv('leaderlist {}/{}_cap/window_{}_day/hold_1_day/{}_{}_cap_window_{}_hold_1_pl.csv'.format(date, cap, win, each, cap, win))
            except FileNotFoundError:
                continue
            to_combine = pd.concat([to_combine, temp], sort = False, ignore_index = True)
        to_combine.loc['total_p&l', 'p&l'] = sum(to_combine.loc[to_combine['window'] == win]['p&l'])
        to_combine.loc['average_pct_change', 'pct_change(%)'] = to_combine['pct_change(%)'].mean()
        to_combine.loc['total_p&l', 'Date'] = 'Total_P&L'
        to_combine.loc['average_pct_change', 'Date'] = 'Average_Pct_Change'
        if not os.path.exists(os.path.dirname('{}_cap/window_{}_day/'.format(cap, win))):
            os.makedirs(os.path.dirname('{}_cap/window_{}_day/'.format(cap, win)))
        to_combine.to_csv('{}_cap/window_{}_day/{}_cap_window_{}_hold_1_pl_summary.csv'.format(cap, win, cap, win), index = False)    

In [35]:
#Generate trading detail for 3-business day
for win in [1, 3]:
    for date in daterange2:
        print(date)
        for cap in ['small', 'mid', 'large']:
            each = date
            each = each[5:]
            each = each.replace('-', '')
            try:
                portfolio = pd.read_csv\
            ('leaderlist {}/{}_cap/window_{}_day/{}_{}_cap_window_{}_symbols.csv'.format(date, cap, win, each, cap, win))
            except FileNotFoundError:
                break
            url = 'https://ondemand.websol.barchart.com/getHistory.csv?apikey=onDemand&symbol={}&startDate={}&endDate={}&type=daily&splits=true&nearby=1&jerq=true&exchange=NYSE%2CAMEX%2CNASDAQ'
            trading_day = daterange1[daterange1.index(date) + 1]
            portfolio = list(portfolio['Symbol'])
            trading_each = trading_day
            trading_each = trading_each[5:]
            trading_each = trading_each.replace('-', '')
            sell_day = datetime.datetime.strptime(daterange1[daterange1.index(trading_day) + 2], "%Y-%m-%d")
            result = pd.DataFrame([], columns = ['symbol', 'win_start', 'win_end', 'actual_pageview', 'average_pageview', \
                                                 'std_100days_rolling', 'actual_pageview_in_std', 'buy_date', 'sell_date', \
                                                 'buy_price', 'sell_price', 'pct_change(%)', 'abs(pct_change(%))', 'window'])
            count = 0
            window_days = []
            while count < win:
                window_days.append(daterange1[daterange1.index(date) - count])
                count += 1
            window_days = window_days[::-1]
            win_start = window_days[0]
            win_end = window_days[-1]
            result['symbol'] = portfolio
            result['win_start'] = str(win_start)[:10]
            result['win_end'] = str(win_end)[:10]
            result['buy_date'] = trading_day
            result['sell_date'] = sell_day
            for i, item in enumerate(portfolio):
                try:
                    buy = pd.read_csv(url.format(item, trading_day, trading_day))
                except EmptyDataError:
                    result.loc[result['symbol'] == item, 'buy_price'] = 'No Trading'
                    continue
                try:
                    sell = pd.read_csv(url.format(item, sell_day, sell_day))
                except EmptyDataError:
                    result.loc[result['symbol'] == item, 'sell_price'] = 'No Trading'
                    continue
                pageview_price = pd.read_csv('pageview_price/pageview_price_{}.csv'.format(item))
                temp = pageview_price['PageView']
                pageview_price['std_100days_rolling'] = (temp.rolling(100).std()).shift(win)
                pageview_price['mean_100days_rolling'] = (temp.rolling(100).mean()).shift(win)
                total_pageview = 0
                for each in window_days:
                    try:
                        total_pageview += int(pageview_price.loc[pageview_price['Date'] == str(each)[:10]]['PageView'])
                    except:
                        page = pd.read_csv('pageview_daily_2018/pageview_daily_{}.csv'.format(item))
                        total_pageview += int(page.loc[page['date'] == str(each)[:10]]['total_page_views'])
                result.loc[i, 'actual_pageview'] = total_pageview
                result.loc[i, 'average_pageview'] = float(pageview_price.loc[pageview_price['Date'] == str(win_end)[:10]]['mean_100days_rolling'])*win
                result.loc[i, 'std_100days_rolling'] = float(pageview_price.loc[pageview_price['Date'] == str(win_end)[:10]]['std_100days_rolling'])
                result.loc[i, 'actual_pageview_in_std'] = float(pageview_price.loc[pageview_price['Date'] == str(win_end)[:10]]['PageView_Change_in_Std_{}'.format(win)])
                result.loc[i, 'buy_price'] = buy.loc[0, 'open']
                result.loc[i, 'sell_price'] = sell.loc[0, 'close']
                result.loc[i, 'pct_change(%)'] = sell.loc[0, 'close']/buy.loc[0, 'open'] - 1)*100
                result.loc[i, 'abs(pct_change(%))'] = abs((sell.loc[0, 'close']/buy.loc[0, 'open'] - 1)*100)
                result.loc[i, 'window'] = win
            if not os.path.exists(os.path.dirname('leaderlist {}/{}_cap/window_{}_day/hold_3_day/'.format(date, cap, win))):
                os.makedirs(os.path.dirname('leaderlist {}/{}_cap/window_{}_day/hold_3_day/'.format(date, cap, win)))
            result.to_csv('leaderlist {}/{}_cap/window_{}_day/hold_3_day/{}_{}_cap_window_{}_hold_3_detail.csv'.format(date, cap, win, trading_each, cap, win), index = False)
            

2018-01-02
2018-01-03
2018-01-04
2018-01-05
2018-01-08
2018-01-09
2018-01-10
2018-01-11
2018-01-12
2018-01-16
2018-01-17
2018-01-18
2018-01-19
2018-01-22
2018-01-23
2018-01-24
2018-01-25
2018-01-26
2018-01-29
2018-01-30
2018-01-31
2018-02-01
2018-02-02
2018-02-05
2018-02-06
2018-02-07
2018-02-08
2018-02-09
2018-02-12
2018-02-13
2018-02-14
2018-02-15
2018-02-16
2018-02-20
2018-02-21
2018-02-22
2018-02-23
2018-02-26
2018-02-27
2018-02-28
2018-03-01
2018-03-02
2018-03-05
2018-03-06
2018-03-07
2018-03-08
2018-03-09
2018-03-12
2018-03-13
2018-03-14
2018-03-15
2018-03-16
2018-03-19
2018-03-20
2018-03-21
2018-03-22
2018-03-23
2018-03-26
2018-03-27
2018-03-28
2018-03-29
2018-04-02
2018-04-03
2018-04-04
2018-04-05
2018-04-06
2018-04-09
2018-04-10
2018-04-11
2018-04-12
2018-04-13
2018-04-16
2018-04-17
2018-04-18
2018-04-19
2018-04-20
2018-04-23
2018-04-24
2018-04-25
2018-04-26
2018-04-27
2018-04-30
2018-05-01
2018-05-02
2018-05-03
2018-05-04
2018-05-07
2018-05-08
2018-05-09
2018-05-10
2018-05-11

In [37]:
daterange2.index('2018-03-01')

40

In [38]:
#Generate trading detail for today close to next day close
for win in [1, 3]:
    for date in daterange2:
        print(date)
        for cap in ['small', 'mid', 'large']:
            each = date
            each = each[5:]
            each = each.replace('-', '')
            try:
                portfolio = pd.read_csv\
            ('leaderlist {}/{}_cap/window_{}_day/{}_{}_cap_window_{}_symbols.csv'.format(date, cap, win, each, cap, win))
            except FileNotFoundError:
                break
            url = 'https://ondemand.websol.barchart.com/getHistory.csv?apikey=onDemand&symbol={}&startDate={}&endDate={}&type=daily&splits=true&nearby=1&jerq=true&exchange=NYSE%2CAMEX%2CNASDAQ'
            trading_day = date
            portfolio = list(portfolio['Symbol'])
            trading_each = trading_day
            trading_each = trading_each[5:]
            trading_each = trading_each.replace('-', '')
            sell_day = daterange1[daterange1.index(trading_day) + 1]
            result = pd.DataFrame([], columns = ['symbol', 'win_start', 'win_end', 'actual_pageview', 'average_pageview', \
                                                 'std_100days_rolling', 'actual_pageview_in_std', 'buy_date', 'sell_date', \
                                                 'buy_price', 'sell_price', 'pct_change(%)', 'abs(pct_change(%))', 'window'])
            temp_win_date = datetime.datetime.strptime(date, "%Y-%m-%d")
            window_days = []
            count = 0
            while count < win:
                window_days.append(daterange1[daterange1.index(date) - count])
                count += 1
            window_days = window_days[::-1]
            win_start = window_days[0]
            win_end = window_days[-1]
            result['symbol'] = portfolio
            result['win_start'] = str(win_start)[:10]
            result['win_end'] = str(win_end)[:10]
            result['buy_date'] = trading_day
            result['sell_date'] = sell_day
            for i, item in enumerate(portfolio):
                try:
                    buy = pd.read_csv(url.format(item, trading_day, trading_day))
                except EmptyDataError:
                    result.loc[result['symbol'] == item, 'buy_price'] == 'No Trading'
                    continue
                try:
                    sell = pd.read_csv(url.format(item, sell_day, sell_day))
                except EmptyDataError:
                    result.loc[result['symbol'] == item, 'sell_price'] == 'No Trading'
                    continue
                price = pd.read_csv(url.format(item, trading_day, sell_day))
                pageview_price = pd.read_csv('pageview_price/pageview_price_{}.csv'.format(item))
                temp = pageview_price['PageView']
                pageview_price['std_100days_rolling'] = (temp.rolling(100).std()).shift(win)
                pageview_price['mean_100days_rolling'] = (temp.rolling(100).mean()).shift(win)
                total_pageview = 0
                for each in window_days:
                    try:
                        total_pageview += int(pageview_price.loc[pageview_price['Date'] == str(each)[:10]]['PageView'])
                    except:
                        page = pd.read_csv('pageview_daily_2018/pageview_daily_{}.csv'.format(item))
                        total_pageview += int(page.loc[page['date'] == str(each)[:10]]['total_page_views'])
                result.loc[i, 'actual_pageview'] = total_pageview
                result.loc[i, 'average_pageview'] = float(pageview_price.loc[pageview_price['Date'] == str(win_end)[:10]]['mean_100days_rolling'])*win
                result.loc[i, 'std_100days_rolling'] = float(pageview_price.loc[pageview_price['Date'] == str(win_end)[:10]]['std_100days_rolling'])
                result.loc[i, 'actual_pageview_in_std'] = float(pageview_price.loc[pageview_price['Date'] == str(win_end)[:10]]['PageView_Change_in_Std_{}'.format(win)])
                result.loc[i, 'buy_price'] = price.loc[0, 'close']
                result.loc[i, 'sell_price'] = price.loc[1, 'close']
                result.loc[i, 'pct_change(%)'] = (price.loc[1, 'close']/price.loc[0, 'close'] - 1)*100
                result.loc[i, 'abs(pct_change(%))'] = abs((price.loc[1, 'close']/price.loc[0, 'close'] - 1)*100)
                result.loc[i, 'window'] = win
            if not os.path.exists(os.path.dirname('leaderlist {}/{}_cap/window_{}_day/hold_1b_day/'.format(date, cap, win))):
                os.makedirs(os.path.dirname('leaderlist {}/{}_cap/window_{}_day/hold_1b_day/'.format(date, cap, win)))
            result.to_csv('leaderlist {}/{}_cap/window_{}_day/hold_1b_day/{}_{}_cap_window_{}_hold_1b_detail.csv'.format(date, cap, win, trading_each, cap, win), index = False)
            

2018-03-01
2018-03-02
2018-03-05
2018-03-06
2018-03-07
2018-03-08
2018-03-09
2018-03-12
2018-03-13
2018-03-14
2018-03-15
2018-03-16
2018-03-19
2018-03-20
2018-03-21
2018-03-22
2018-03-23
2018-03-26
2018-03-27
2018-03-28
2018-03-29
2018-04-02
2018-04-03
2018-04-04
2018-04-05
2018-04-06
2018-04-09
2018-04-10
2018-04-11
2018-04-12
2018-04-13
2018-04-16
2018-04-17
2018-04-18
2018-04-19
2018-04-20
2018-04-23
2018-04-24
2018-04-25
2018-04-26
2018-04-27
2018-04-30
2018-05-01
2018-05-02
2018-05-03
2018-05-04
2018-05-07
2018-05-08
2018-05-09
2018-05-10
2018-05-11
2018-05-14
2018-05-15
2018-05-16
2018-05-17
2018-05-18
2018-05-21
2018-05-22
2018-05-23
2018-05-24
2018-05-25
2018-05-29
2018-05-30
2018-05-31
2018-06-01
2018-06-04
2018-06-05
2018-06-06
2018-06-07
2018-06-08
2018-06-11
2018-06-12
2018-06-13
2018-06-14
2018-06-15
2018-06-18
2018-06-19
2018-06-20
2018-06-21
2018-06-22
2018-06-25
2018-06-26
2018-06-27
2018-06-28
2018-06-29
2018-07-02
2018-07-03
2018-07-05
2018-07-06
2018-07-09
2018-07-10

###Please run Concat_Details before running below scrips.

In [208]:
#adding pct_change
for hold in [1, '1b', 3]:
    for cap in ['small', 'mid', 'large']:
        for win in [1, 3]:
            t1 = pd.read_csv('detail_summary/hold_{}_day/{}_cap_window_{}_detail_summary.csv'.format(hold, cap, win))
            t1['temp1'] = t1['buy_price']
            t1['temp2'] = t1['sell_price']
            try:
                t1.loc[t1['buy_price'] == 'No Trading', 'temp1'] = 0.0001
                t1.loc[t1['buy_price'] == 'No Trading', 'temp2'] = 0
            except TypeError:
                pass
            try:
                t1.loc[t1['sell_price'] == 'No Trading', 'temp2'] = 0
            except TypeError:
                pass
            t1['pct_change(%)'] = (t1['temp2'].apply(float)/t1['temp1'].apply(float) - 1)*100
            t1['abs(pct_change(%))'] = abs(t1['pct_change(%)'])
            t1.drop(columns = ['window', 'temp1', 'temp2'], axis = 1, inplace = True)
            t1['window'] = win
            t1.to_csv('detail_summary/hold_{}_day/{}_cap_window_{}_detail_summary.csv'.format(hold, cap, win), index = False)


In [209]:
#add sentiment data
sse = pd.read_csv('sample_data_SMA/sma_sentiment_equities.csv')
sse = sse[['Date', 'Symbol', 's-score', 's', 's-mean']]
sse.columns = ['win_end', 'symbol', 's-score', 's', 's-mean']
for hold in [1, '1b', '3']:
    for cap in ['small', 'mid', 'large']:
        for win in [1, 3]:
            ds = pd.read_csv('detail_summary/hold_{}_day/{}_cap_window_{}_detail_summary.csv'.format(hold, cap, win))
            ds = ds.merge(sse, on = ['win_end', 'symbol'])
            ds['buy?'] = 0
            ds.loc[ds['s-score'] > 1, 'buy?'] = 1
            #print(ds.head())
            ds.to_csv('detail_summary/hold_{}_day/{}_cap_window_{}_detail_summary.csv'.\
                      format(hold, cap, win), index = False)

In [210]:
#set no trading
for hold in [1, '1b', '3']:
    for cap in ['small', 'mid', 'large']:
        for win in [1, 3]:
            ds = pd.read_csv('detail_summary/hold_{}_day/{}_cap_window_{}_detail_summary.csv'.format(hold, cap, win))
            try:
                ds.loc[ds['buy_price'] == 'No Trading', 'abs(pct_change(%))'] = 0
                ds.loc[ds['buy_price'] == 'No Trading', 'pct_change(%)'] = 0
            except:
                pass
            try:
                ds.loc[ds['sell_price'] == 'No Trading', 'abs(pct_change(%))'] = 0
                ds.loc[ds['sell_price'] == 'No Trading', 'pct_change(%)'] = 0
            except:
                pass
            ds.to_csv('detail_summary/hold_{}_day/{}_cap_window_{}_detail_summary.csv'.\
                      format(hold, cap, win), index = False)

In [211]:
url_index = 'https://ondemand.websol.barchart.com/getHistory.csv?apikey=ondemand&symbol={}&type=daily&startDate=2018-01-01&endDate=2018-12-31&maxRecords=1000&order=asc&sessionFilter=EFK&splits=true&volume=sum'

In [212]:
import numpy as np

In [213]:
#adding pct changes for sp500
sp500 = pd.read_csv(url_index.format('$SPX'))
sp500 = sp500.iloc[:, [0, 2, 3, 6]]
sp500['sp500_abs(1_day_pct_change(%))'] = abs((sp500['close']/sp500['open'] - 1)*100)
temp = (sp500['close'].pct_change(1)*100).fillna(0)
temp = abs(temp.apply(float))
temp[0] = np.nan
sp500['sp500_abs(1b_day_pct_change(%))'] = temp
temp1 = abs(((sp500['close']/sp500['open'].shift(2) - 1)*100).fillna(0))
temp1[0] = np.nan
temp1[1] = np.nan
sp500['sp500_abs(3_day_pct_change(%))'] = temp1

In [214]:
#adding pct changes for russell2000
russell_2000 = pd.read_csv(url_index.format('IWM'))
russell_2000 = russell_2000.iloc[:, [0, 2, 3, 6]]
russell_2000['russell_2000_abs(1_day_pct_change(%))'] = abs((russell_2000['close']/russell_2000['open'] - 1)*100)
temp = (russell_2000['close'].pct_change(1)*100).fillna(0)
temp = abs(temp.apply(float))
temp[0] = np.nan
russell_2000['russell_2000_abs(1b_day_pct_change(%))'] = temp
temp1 = abs(((russell_2000['close']/russell_2000['open'].shift(2) - 1)*100).fillna(0))
temp1[0] = np.nan
temp1[1] = np.nan
russell_2000['russell_2000_abs(3_day_pct_change(%))'] = temp1

In [217]:
for hold in [1, '1b', 3]:
    for cap in ['small', 'mid', 'large']:
        for win in [1, 3]:
            ds = pd.read_csv('detail_summary/hold_{}_day/{}_cap_window_{}_detail_summary.csv'.format(hold, cap, win))
            if cap == 'small':
                if hold == 1:
                    temp2 = russell_2000[['tradingDay', 'russell_2000_abs(1_day_pct_change(%))']].copy()
                elif hold == 3:
                    temp2 = russell_2000[['tradingDay', 'russell_2000_abs(3_day_pct_change(%))']].copy()
                elif hold == '1b':
                    temp2 = russell_2000[['tradingDay', 'russell_2000_abs(1b_day_pct_change(%))']].copy()
            else:
                if hold == 1:
                    temp2 = sp500[['tradingDay', 'sp500_abs(1_day_pct_change(%))']].copy()
                elif hold == 3:
                    temp2 = sp500[['tradingDay', 'sp500_abs(3_day_pct_change(%))']].copy()
                elif hold == '1b':
                    temp2 = sp500[['tradingDay', 'sp500_abs(1b_day_pct_change(%))']].copy()
            temp2.rename(columns = {'tradingDay' : 'sell_date'}, inplace = True)
            ds = ds.merge(temp2, on = 'sell_date')
            ds = ds.iloc[:, [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 18, 13, 12, 14, 15, 16, 17]]
            #print(ds.head())
            #ds.to_csv('detail_summary/hold_{}_day/{}_cap_window_{}_detail_summary.csv'.\
                      #format(hold, cap, win), index = False)